# IBM Applied Data Science Capstone Course by Coursera
## Week 5 Final Report
### Opening a Pizza Shop  in Chennai, India

- Build a dataframe of neighborhoods in chennai, India by web scraping the data from Wikipedia page 
- Get the geographical coordinates of the neighborhoods
- Obtain the venue data for the neighborhoods from Foursquare API
- Explore and cluster the neighborhoods
- Select the best cluster to open a Pizza shop in Chennai

### Installing geocoder and folium package

In [1]:
!pip install geocoder

In [2]:
!pip install folium

## 1. Import libraries

In [3]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library

print("Libraries imported.")

Libraries imported.


## 2. Scrap data from Wikipedia page into a DataFrame

In [4]:
# send the GET request
response = requests.get("https://en.wikipedia.org/wiki/List_of_neighbourhoods_of_Chennai").text

In [5]:
# parse data from the html into a beautifulsoup object
soup = BeautifulSoup(response, 'html.parser')
soup


<!DOCTYPE html>

<html class="client-nojs" dir="ltr" lang="en">
<head>
<meta charset="utf-8"/>
<title>List of neighbourhoods of Chennai - Wikipedia</title>
<script>document.documentElement.className="client-js";RLCONF={"wgBreakFrames":!1,"wgSeparatorTransformTable":["",""],"wgDigitTransformTable":["",""],"wgDefaultDateFormat":"dmy","wgMonthNames":["","January","February","March","April","May","June","July","August","September","October","November","December"],"wgRequestId":"Xr2gUQpAIEIAAIYHY@YAAAEE","wgCSPNonce":!1,"wgCanonicalNamespace":"","wgCanonicalSpecialPageName":!1,"wgNamespaceNumber":0,"wgPageName":"List_of_neighbourhoods_of_Chennai","wgTitle":"List of neighbourhoods of Chennai","wgCurRevisionId":948960191,"wgRevisionId":948960191,"wgArticleId":9736473,"wgIsArticle":!0,"wgIsRedirect":!1,"wgAction":"view","wgUserName":null,"wgUserGroups":["*"],"wgCategories":["Use dmy dates from February 2019","Use Indian English from February 2019","All Wikipedia articles written in Indian Eng

In [6]:
names = soup.find_all('td',class_ ='navbox-list navbox-odd hlist')[0].find_all('a')
names

[<a href="/wiki/Adyar,_Chennai" title="Adyar, Chennai">Adyar</a>,
 <a href="/wiki/Adambakkam" title="Adambakkam">Adambakkam</a>,
 <a href="/wiki/Alapakkam" title="Alapakkam">Alapakkam</a>,
 <a href="/wiki/Alandur" title="Alandur">Alandur</a>,
 <a href="/wiki/Alwarpet" title="Alwarpet">Alwarpet</a>,
 <a href="/wiki/Alwarthirunagar" title="Alwarthirunagar">Alwarthirunagar</a>,
 <a href="/wiki/Ambattur" title="Ambattur">Ambattur</a>,
 <a href="/wiki/Aminjikarai" title="Aminjikarai">Aminjikarai</a>,
 <a href="/wiki/Anna_Nagar" title="Anna Nagar">Anna Nagar</a>,
 <a href="/wiki/Anna_Nagar_West" title="Anna Nagar West">Anna Nagar West</a>,
 <a href="/wiki/Annanur" title="Annanur">Annanur</a>,
 <a class="mw-redirect" href="/wiki/Andarkuppam,_Chennai" title="Andarkuppam, Chennai">Andarkuppam</a>,
 <a href="/wiki/Arumbakkam" title="Arumbakkam">Arumbakkam</a>,
 <a href="/wiki/Ashok_Nagar,_Chennai" title="Ashok Nagar, Chennai">Ashok Nagar</a>,
 <a href="/wiki/Athipattu" title="Athipattu">Athipatt

In [7]:
# create a list to store neighborhood data
neighborhoodList = []
# append the data into the list
for title in names:
    neighborhoodList.append(title.text)

In [8]:

# create a new DataFrame from the list
chennai_df = pd.DataFrame({"Neighborhood": neighborhoodList})
chennai_df.head()

Neighborhood
0        Adyar
1   Adambakkam
2    Alapakkam
3      Alandur
4     Alwarpet

In [9]:
# print the number of rows of the dataframe
chennai_df.shape

(172, 1)

## 3. Get the geographical coordinates

In [10]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Chennai, India'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [11]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in chennai_df["Neighborhood"].tolist() ]

In [12]:
coords

[[13.00305000000003, 80.25193000000007],
 [12.99192000000005, 80.20603000000006],
 [13.046100000000024, 80.16499000000005],
 [13.00013000000007, 80.20060000000007],
 [13.034710000000075, 80.25416000000007],
 [13.050550000000044, 80.18397000000004],
 [13.118820000000028, 80.15442000000007],
 [13.071390000000065, 80.22256000000004],
 [13.083590000000072, 80.21020000000004],
 [13.092720000000043, 80.20222000000007],
 [13.112120000000061, 80.12895000000003],
 [13.191590000000076, 80.27328000000006],
 [13.073080000000061, 80.20952000000005],
 [13.035390000000064, 80.21220000000005],
 [13.256700000000023, 80.29109000000005],
 [13.129090000000076, 80.10361000000006],
 [13.09883000000002, 80.23238000000003],
 [12.996850000000052, 80.26691000000005],
 [13.064400000000035, 80.28065000000004],
 [13.040270000000021, 80.06437000000005],
 [12.682240000000036, 79.98008000000004],
 [13.072880000000055, 80.24567000000008],
 [12.932770000000062, 80.14387000000005],
 [13.090240000000051, 80.2655700000000

In [13]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [14]:
# merge the coordinates into the original dataframe
chennai_df['Latitude'] = df_coords['Latitude']
chennai_df['Longitude'] = df_coords['Longitude']

In [15]:
# check the neighborhoods and the coordinates
print(chennai_df.shape)
chennai_df

(172, 3)


Neighborhood   Latitude  Longitude
0                     Adyar  13.003050  80.251930
1                Adambakkam  12.991920  80.206030
2                 Alapakkam  13.046100  80.164990
3                   Alandur  13.000130  80.200600
4                  Alwarpet  13.034710  80.254160
5           Alwarthirunagar  13.050550  80.183970
6                  Ambattur  13.118820  80.154420
7               Aminjikarai  13.071390  80.222560
8                Anna Nagar  13.083590  80.210200
9           Anna Nagar West  13.092720  80.202220
10                  Annanur  13.112120  80.128950
11              Andarkuppam  13.191590  80.273280
12               Arumbakkam  13.073080  80.209520
13              Ashok Nagar  13.035390  80.212200
14                Athipattu  13.256700  80.291090
15                    Avadi  13.129090  80.103610
16               Ayanavaram  13.098830  80.232380
17             Besant Nagar  12.996850  80.266910
18                  Chepauk  13.064400  80.280650
19          Chembarambakkam  13.040270  80.064370
20             Chengalpattu  12.682240  79.980080
21                  Chetput  13.072880  80.245670
22             Chitlapakkam  12.932770  80.143870
23                  Choolai  13.090240  80.265570
24              Choolaimedu  13.056760  80.227460
25                Chromepet  12.952340  80.144110
26            Edayanchavadi  13.220800  80.272940
27                   Egmore  13.074280  80.259200
28                   Ennore  13.226280  80.325990
29                 Ernavoor  13.187880  80.308310
30         Foreshore Estate  13.023790  80.275020
31               Georgetown  13.098030  80.290510
32           Greenways Road  13.020865  80.269917
33             Guduvancheri  12.837900  80.053270
34            Gummidipoondi  13.412750  80.126820
35                   Guindy  13.004020  80.220210
36        Guindy TVK Estate  13.004020  80.220210
37               ICF Colony  13.094620  80.218390
38              Injambakkam  12.926370  80.250250
39              Irumbuliyur  12.914320  80.106040
40          Irungattukottai  12.995350  80.004300
41               The Island  13.101260  80.283790
42              K. K. Nagar  13.195220  80.161810
43               Karapakkam  12.915950  80.231920
44                Karanodai  13.249680  80.156230
45              Kathivakkam  13.194370  80.204710
46           Kattankulathur  12.812950  80.031880
47            Kavaraipettai  13.350000  80.150000
48              Kelambakkam  12.793410  80.220100
49                  Kilpauk  13.081980  80.244480
50              Kodambakkam  13.051520  80.224210
51              Kodungaiyur  13.136630  80.244790
52                 Kolathur  13.131830  80.199280
53                 Korattur  13.096050  80.052920
54                 Kosappur  13.183260  80.240590
55              Kottivakkam  12.973550  80.259140
56              Kotturpuram  13.016960  80.242760
57                  Kovalam  12.789840  80.249140
58            Kovilambakkam  12.940470  80.187120
59                Koyambedu  13.066050  80.197230
60               Kundrathur  12.988020  80.106050
61              Madambakkam  12.905290  80.153520
62               Madipakkam  12.964480  80.208700
63               Madhavaram  13.150430  80.234170
64   Madhavaram Milk Colony  13.157520  80.242830
65              Maduravoyal  13.058410  80.166360
66             Mamallapuram  12.785039  80.249871
67                   Manali  13.168640  80.272240
68          Manali New Town  13.203710  80.268540
69               Manapakkam  13.011880  80.171560
70               Mandavelli  13.155760  80.230480
71                  Mangadu  13.030600  80.109030
72             Manjambakkam  13.165560  80.229020
73         Maraimalai Nagar  12.806560  80.041930
74                   Mathur  13.168100  80.244970
75               Medavakkam  12.920090  80.191630
76             Meenambakkam  12.986460  80.176000
77                   Minjur  13.278730  80.261770
78                Mogappair  13.080530  80.161160
79             

In [16]:

# save the DataFrame as CSV file
chennai_df.to_csv("kl_df.csv", index=False)

## 4.Create a map of Chennai with neighborhoods superimposed on top

In [17]:
# get the coordinates of chennai
address = 'Chennai, India'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Chennai, India {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Chennai, India 13.0801721, 80.2838331.


In [18]:
# create map of chennai using latitude and longitude values
map_chennai = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, neighborhood in zip(chennai_df['Latitude'], chennai_df['Longitude'], chennai_df['Neighborhood']):
    label = '{}'.format(neighborhood)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_chennai)  
    
map_chennai

## 5. Use the Foursquare API to explore the neighborhoods

In [24]:

# define Foursquare Credentials and Version
CLIENT_ID = '3KCFLKV10BGADE35JYXJEACPO1EOBGFP1DMWFVYLCJJ4M24J' # your Foursquare ID
CLIENT_SECRET = 'D203QG2GQMQ0UWVTDANABZO12S5U4GFP4NOP3QTTJPKWVJWU' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version


### Now, let's get the top 100 venues that are within a radius of 2000 meters.

In [25]:
radius = 2000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(chennai_df['Latitude'], chennai_df['Longitude'], chennai_df['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [28]:

# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'VenueName', 'VenueLatitude', 'VenueLongitude', 'VenueCategory']

print(venues_df.shape)
venues_df

(5249, 7)


Neighborhood   Latitude  Longitude  \
0                      Adyar  13.003050  80.251930   
1                      Adyar  13.003050  80.251930   
2                      Adyar  13.003050  80.251930   
3                      Adyar  13.003050  80.251930   
4                      Adyar  13.003050  80.251930   
5                      Adyar  13.003050  80.251930   
6                      Adyar  13.003050  80.251930   
7                      Adyar  13.003050  80.251930   
8                      Adyar  13.003050  80.251930   
9                      Adyar  13.003050  80.251930   
10                     Adyar  13.003050  80.251930   
11                     Adyar  13.003050  80.251930   
12                     Adyar  13.003050  80.251930   
13                     Adyar  13.003050  80.251930   
14                     Adyar  13.003050  80.251930   
15                     Adyar  13.003050  80.251930   
16                     Adyar  13.003050  80.251930   
17                     Adyar  13.003050  80.251930   
18                     Adyar  13.003050  80.251930   
19                     Adyar  13.003050  80.251930   
20                     Adyar  13.003050  80.251930   
21                     Adyar  13.003050  80.251930   
22                     Adyar  13.003050  80.251930   
23                     Adyar  13.003050  80.251930   
24                     Adyar  13.003050  80.251930   
25                     Adyar  13.003050  80.251930   
26                     Adyar  13.003050  80.251930   
27                     Adyar  13.003050  80.251930   
28                     Adyar  13.003050  80.251930   
29                     Adyar  13.003050  80.251930   
30                     Adyar  13.003050  80.251930   
31                     Adyar  13.003050  80.251930   
32                     Adyar  13.003050  80.251930   
33                     Adyar  13.003050  80.251930   
34                     Adyar  13.003050  80.251930   
35                     Adyar  13.003050  80.251930   
36                     Adyar  13.003050  80.251930   
37                     Adyar  13.003050  80.251930   
38                     Adyar  13.003050  80.251930   
39                     Adyar  13.003050  80.251930   
40                     Adyar  13.003050  80.251930   
41                     Adyar  13.003050  80.251930   
42                     Adyar  13.003050  80.251930   
43                     Adyar  13.003050  80.251930   
44                     Adyar  13.003050  80.251930   
45                     Adyar  13.003050  80.251930   
46                     Adyar  13.003050  80.251930   
47                     Adyar  13.003050  80.251930   
48                     Adyar  13.003050  80.251930   
49                     Adyar  13.003050  80.251930   
50                     Adyar  13.003050  80.251930   
51                     Adyar  13.003050  80.251930   
52                     Adyar  13.003050  80.251930   
53                     Adyar  13.003050  80.251930   
54                     Adyar  13.003050  80.251930   
55                     Adyar  13.003050  80.251930   
56                     Adyar  13.003050  80.251930   
57                     Adyar  13.003050  80.251930   
58                     Adyar  13.003050  80.251930   
59                     Adyar  13.003050  80.251930   
60                     Adyar  13.003050  80.251930   
61                     Adyar  13.003050  80.251930   
62                     Adyar  13.003050  80.251930   
63                     Adyar  13.003050  80.251930   
64                     Adyar  13.003050  80.251930   
65                     Adyar  13.003050  80.251930   
66                     Adyar  13.003050  80.251930   
67                     Adyar  13.003050  80.251930   
68                     Adyar  13.003050  80.251930   
69                     Adyar  13.003050  80.251930   
70                     Adyar  13.003050  80.251930   
71                     Adyar  13.003050  80.251930   
72                     Adyar  13.003050  80.251930   
73                  

###  Let's check how many venues were returned for each neighorhood

In [29]:
venues_df.groupby(["Neighborhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  \
Neighborhood                                                            
Adambakkam                    72         72         72             72   
Adyar                         85         85         85             85   
Alandur                       49         49         49             49   
Alapakkam                     24         24         24             24   
Alwarpet                     100        100        100            100   
Alwarthirunagar               31         31         31             31   
Ambattur                      12         12         12             12   
Aminjikarai                   90         90         90             90   
Andarkuppam                    1          1          1              1   
Anna Nagar                   100        100        100            100   
Anna Nagar West               90         90         90             90   
Annanur                        5          5          5              5   
Arumbakkam                   100        100        100            100   
Ashok Nagar                   69         69         69             69   
Athipattu                      2          2          2              2   
Avadi                          4          4          4              4   
Ayanavaram                    28         28         28             28   
Besant Nagar                  89         89         89             89   
Chembarambakkam                7          7          7              7   
Chengalpattu                   8          8          8              8   
Chepauk                       69         69         69             69   
Chetput                      100        100        100            100   
Chitlapakkam                  15         15         15             15   
Choolai                       42         42         42             42   
Choolaimedu                   99         99         99             99   
Chromepet                     18         18         18             18   
Edayanchavadi                  3          3          3              3   
Egmore                       100        100        100            100   
Ennore                         5          5          5              5   
Ernavoor                       5          5          5              5   
Foreshore Estate              40         40         40             40   
Georgetown                    14         14         14             14   
Greenways Road                62         62         62             62   
Guduvancheri                  20         20         20             20   
Guindy                        68         68         68             68   
Guindy TVK Estate             68         68         68             68   
Gummidipoondi                  4          4          4              4   
ICF Colony                    74         74         74             74   
Injambakkam                   14         14         14             14   
Irumbuliyur                    8          8          8              8   
Irungattukottai                5          5          5              5   
K. K. Nagar                    4          4          4              4   
Karanodai                      3          3          3              3   
Karapakkam                    31         31         31             31   
Kathivakkam                    2          2          2              2   
Kattankulathur                13         13         13             13   
Kavaraipettai                  2          2          2              2   
Kelambakkam                    5          5          5              5   
Kilpauk                       57         57         57             57   
Kodambakkam                  100        100        100            100   
Kodungaiyur                   10         10         10             10   
Kolathur                       7          7          7              7   
Korattur                       3          3          3              3   
Kosappur 

###  Let's find out how many unique categories can be curated from all the returned venues

In [30]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 193 uniques categories.


In [31]:

# print out the list of categories
venues_df['VenueCategory'].unique()[:]

array(['Café', 'Indian Restaurant', 'North Indian Restaurant',
       'Ice Cream Shop', 'Vegetarian / Vegan Restaurant', "Women's Store",
       'Bookstore', 'Middle Eastern Restaurant', 'Pizza Place',
       'Chinese Restaurant', 'Fast Food Restaurant', 'Juice Bar',
       'Clothing Store', 'Asian Restaurant', 'Dessert Shop', 'Rock Club',
       'Italian Restaurant', 'Bistro', 'Lounge',
       'Mediterranean Restaurant', 'Movie Theater', 'Department Store',
       'Coffee Shop', 'Grocery Store', 'Snack Place',
       'Fruit & Vegetable Store', 'College Cafeteria',
       'Performing Arts Venue', 'Sandwich Place', 'Gym',
       'Comfort Food Restaurant', 'Hotel', 'Office', 'Diner',
       'Breakfast Spot', 'Multiplex', 'Hotel Bar', 'Motorcycle Shop',
       'Light Rail Station', 'Market', 'Shopping Mall',
       'Rajasthani Restaurant', 'Donut Shop', "Men's Store", 'Bar',
       'Train Station', 'Restaurant', 'Punjabi Restaurant',
       'Frozen Yogurt Shop', 'BBQ Joint', 'Mexican Rest

In [32]:

# check if the results contain "pizza shops"
"Pizza Place" in venues_df['VenueCategory'].unique()

True

## 6. Analyze Each Neighborhood

In [33]:

# one hot encoding
chennai_onehot = pd.get_dummies(venues_df[['VenueCategory']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
chennai_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [chennai_onehot.columns[-1]] + list(chennai_onehot.columns[:-1])
chennai_onehot = chennai_onehot[fixed_columns]

print(chennai_onehot.shape)
chennai_onehot.head()

(5249, 194)


Neighborhoods  ATM  Accessories Store  Afghan Restaurant  \
0         Adyar    0                  0                  0   
1         Adyar    0                  0                  0   
2         Adyar    0                  0                  0   
3         Adyar    0                  0                  0   
4         Adyar    0                  0                  0   

   African Restaurant  Airport Lounge  Airport Service  Airport Terminal  \
0                   0               0                0                 0   
1                   0               0                0                 0   
2                   0               0                0                 0   
3                   0               0                0                 0   
4                   0               0                0                 0   

   American Restaurant  Andhra Restaurant  Arcade  Art Gallery  \
0                    0                  0       0            0   
1                    0                  0       0            0   
2                    0                  0       0            0   
3                    0                  0       0            0   
4                    0                  0       0            0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Workshop  \
0                    0                 0                   0              0   
1                    0                 0                   0              0   
2                    0                 0                   0              0   
3                    0                 0                   0              0   
4                    0                 0                   0              0   

   BBQ Joint  Badminton Court  Bakery  Bank  Bar  Beach  Bengali Restaurant  \
0          0                0       0     0    0      0                   0   
1          0                0       0     0    0      0                   0   
2          0                0       0     0    0      0                   0   
3          0                0       0     0    0      0                   0   
4          0                0       0     0    0      0                   0   

   Big Box Store  Bike Rental / Bike Share  Bistro  Boat or Ferry  Bookstore  \
0              0                         0       0              0          0   
1              0                         0       0              0          0   
2              0                         0       0              0          0   
3              0                         0       0              0          0   
4              0                         0       0              0          0   

   Boutique  Bowling Alley  Breakfast Spot  Buffet  Burger Joint  \
0         0              0               0       0             0   
1         0              0               0       0             0   
2         0              0               0       0             0   
3         0              0               0       0             0   
4         0              0               0       0             0   

   Burmese Restaurant  Bus Line  Bus Station  Cafeteria  Café  Campground  \
0                   0         0            0          0     1           0   
1                   0         0            0          0     0           0   
2                   0         0            0          0     0           0   
3                   0         0            0          0     0           0   
4                   0         0            0          0     0           0   

   Chinese Restaurant  Chocolate Shop  Church  Clothing Store  Cocktail Bar  \
0                   0               0       0               0             0   
1                   0               0       0               0             0   
2                   0               0       0               0             0   
3                   0               0       0               0             0   
4                   0               0       0               0             0  

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [34]:

chennai_grouped = chennai_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(chennai_grouped.shape)
chennai_grouped

(170, 194)


Neighborhoods       ATM  Accessories Store  Afghan Restaurant  \
0                Adambakkam  0.000000           0.000000           0.000000   
1                     Adyar  0.000000           0.000000           0.000000   
2                   Alandur  0.000000           0.000000           0.000000   
3                 Alapakkam  0.000000           0.000000           0.000000   
4                  Alwarpet  0.000000           0.000000           0.000000   
5           Alwarthirunagar  0.000000           0.000000           0.000000   
6                  Ambattur  0.000000           0.000000           0.000000   
7               Aminjikarai  0.000000           0.000000           0.000000   
8               Andarkuppam  1.000000           0.000000           0.000000   
9                Anna Nagar  0.000000           0.000000           0.000000   
10          Anna Nagar West  0.000000           0.000000           0.000000   
11                  Annanur  0.000000           0.000000           0.000000   
12               Arumbakkam  0.000000           0.000000           0.000000   
13              Ashok Nagar  0.000000           0.000000           0.000000   
14                Athipattu  0.000000           0.000000           0.000000   
15                    Avadi  0.000000           0.000000           0.000000   
16               Ayanavaram  0.000000           0.000000           0.000000   
17             Besant Nagar  0.000000           0.000000           0.000000   
18          Chembarambakkam  0.000000           0.000000           0.000000   
19             Chengalpattu  0.000000           0.000000           0.000000   
20                  Chepauk  0.000000           0.000000           0.000000   
21                  Chetput  0.000000           0.000000           0.000000   
22             Chitlapakkam  0.000000           0.000000           0.000000   
23                  Choolai  0.000000           0.000000           0.000000   
24              Choolaimedu  0.000000           0.000000           0.000000   
25                Chromepet  0.000000           0.000000           0.055556   
26            Edayanchavadi  0.000000           0.000000           0.000000   
27                   Egmore  0.000000           0.000000           0.000000   
28                   Ennore  0.200000           0.000000           0.000000   
29                 Ernavoor  0.000000           0.000000           0.000000   
30         Foreshore Estate  0.000000           0.000000           0.000000   
31               Georgetown  0.000000           0.000000           0.000000   
32           Greenways Road  0.000000           0.000000           0.000000   
33             Guduvancheri  0.000000           0.000000           0.000000   
34                   Guindy  0.000000           0.000000           0.000000   
35        Guindy TVK Estate  0.000000           0.000000           0.000000   
36            Gummidipoondi  0.500000           0.000000           0.000000   
37               ICF Colony  0.000000           0.000000           0.000000   
38              Injambakkam  0.000000           0.000000           0.000000   
39              Irumbuliyur  0.000000           0.000000           0.000000   
40          Irungattukottai  0.000000           0.000000           0.000000   
41              K. K. Nagar  0.000000           0.000000           0.000000   
42                Karanodai  0.333333           0.000000           0.000000   
43               Karapakkam  0.000000           0.000000           0.032258   
44              Kathivakkam  0.000000           0.000000           0.000000   
45           Kattankulathur  0.076923           0.000000           0.000000   
46            Kavaraipettai  0.500000           0.000000           0.000000   
47              Kelambakkam  0.000000           0.000000           0.000000   
48                  Kilpauk  0.000000           0.000000           0.000000   
49              Kodambakkam  0.000000           0.000000        

In [35]:
len(chennai_grouped[chennai_grouped["Pizza Place"] > 0])

92

### Create a new DataFrame for Pizza shop data only

In [36]:

chennai_pizzas_shop = chennai_grouped[["Neighborhoods","Pizza Place"]]
chennai_pizzas_shop.head()

Neighborhoods  Pizza Place
0    Adambakkam     0.083333
1         Adyar     0.058824
2       Alandur     0.040816
3     Alapakkam     0.083333
4      Alwarpet     0.000000

## 7. Cluster Neighborhoods
Run k-means to cluster the neighborhoods in chennai into 3 clusters

In [37]:
# set number of clusters
kclusters = 3

chennai_clustering = chennai_pizzas_shop.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(chennai_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 1, 0, 0, 1, 1, 0], dtype=int32)

In [38]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
chennai_merged = chennai_pizzas_shop.copy()

# add clustering labels
chennai_merged["Cluster Labels"] = kmeans.labels_
chennai_merged 

Neighborhoods  Pizza Place  Cluster Labels
0                Adambakkam     0.083333               0
1                     Adyar     0.058824               0
2                   Alandur     0.040816               0
3                 Alapakkam     0.083333               0
4                  Alwarpet     0.000000               1
5           Alwarthirunagar     0.096774               0
6                  Ambattur     0.083333               0
7               Aminjikarai     0.022222               1
8               Andarkuppam     0.000000               1
9                Anna Nagar     0.040000               0
10          Anna Nagar West     0.044444               0
11                  Annanur     0.000000               1
12               Arumbakkam     0.040000               0
13              Ashok Nagar     0.072464               0
14                Athipattu     0.000000               1
15                    Avadi     0.000000               1
16               Ayanavaram     0.035714               1
17             Besant Nagar     0.056180               0
18          Chembarambakkam     0.000000               1
19             Chengalpattu     0.000000               1
20                  Chepauk     0.014493               1
21                  Chetput     0.030000               1
22             Chitlapakkam     0.200000               2
23                  Choolai     0.047619               0
24              Choolaimedu     0.030303               1
25                Chromepet     0.111111               0
26            Edayanchavadi     0.000000               1
27                   Egmore     0.030000               1
28                   Ennore     0.000000               1
29                 Ernavoor     0.000000               1
30         Foreshore Estate     0.025000               1
31               Georgetown     0.000000               1
32           Greenways Road     0.016129               1
33             Guduvancheri     0.050000               0
34                   Guindy     0.044118               0
35        Guindy TVK Estate     0.044118               0
36            Gummidipoondi     0.000000               1
37               ICF Colony     0.040541               0
38              Injambakkam     0.071429               0
39              Irumbuliyur     0.125000               0
40          Irungattukottai     0.000000               1
41              K. K. Nagar     0.000000               1
42                Karanodai     0.000000               1
43               Karapakkam     0.064516               0
44              Kathivakkam     0.000000               1
45           Kattankulathur     0.000000               1
46            Kavaraipettai     0.000000               1
47              Kelambakkam     0.200000               2
48                  Kilpauk     0.052632               0
49              Kodambakkam     0.040000               0
50              Kodungaiyur     0.100000               0
51                 Kolathur     0.000000               1
52                 Korattur     0.000000               1
53                 Kosappur     0.000000               1
54              Kottivakkam     0.031746               1
55              Kotturpuram     0.010526               1
56                  Kovalam     0.000000               1
57            Kovilambakkam     0.200000               2
58                Koyambedu     0.037037               1
59               Kundrathur     0.000000               1
60              Madambakkam     0.200000               2
61               Madhavaram     0.000000               1
62   Madhavaram Milk Colony     0.000000               1
63               Madipakkam     0.027778               1
64              Maduravoyal     0.125000               0
65             Mamallapuram     0.000000               1
66                   Manali     0.000000               1
67          Manali New Town     0.000000               1
68               Manapakkam     0.000000               1
69               Mandave

In [39]:
chennai_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
chennai_merged.head()

Neighborhood  Pizza Place  Cluster Labels
0   Adambakkam     0.083333               0
1        Adyar     0.058824               0
2      Alandur     0.040816               0
3    Alapakkam     0.083333               0
4     Alwarpet     0.000000               1

In [40]:
# merge chennai_grouped with chennai_data to add latitude/longitude for each neighborhood
chennai_merged = chennai_merged.join(chennai_df.set_index("Neighborhood"), on="Neighborhood")

print(chennai_merged.shape)
chennai_merged.head() # check the last columns!

(170, 5)


Neighborhood  Pizza Place  Cluster Labels  Latitude  Longitude
0   Adambakkam     0.083333               0  12.99192   80.20603
1        Adyar     0.058824               0  13.00305   80.25193
2      Alandur     0.040816               0  13.00013   80.20060
3    Alapakkam     0.083333               0  13.04610   80.16499
4     Alwarpet     0.000000               1  13.03471   80.25416

In [41]:

# sort the results by Cluster Labels
print(chennai_merged.shape)
chennai_merged.sort_values(["Cluster Labels"], inplace=True)
chennai_merged

(170, 5)


Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
0                Adambakkam     0.083333               0  12.991920  80.206030
104                Perambur     0.083333               0  13.122470  80.235690
103          Peerkankaranai     0.111111               0  12.912240  80.098950
96                   Pammal     0.086957               0  12.968140  80.133590
94               Pallavaram     0.111111               0  12.974440  80.148520
93           Palavanthangal     0.095238               0  12.986810  80.186730
91                     Padi     0.045455               0  13.097560  80.186790
89                 Nolambur     0.062500               0  13.076260  80.171690
88               Nesapakkam     0.090909               0  13.035210  80.191770
75             Meenambakkam     0.060606               0  12.986460  80.176000
74               Medavakkam     0.090909               0  12.920090  80.191630
64              Maduravoyal     0.125000               0  13.058410  80.166360
50              Kodungaiyur     0.100000               0  13.136630  80.244790
49              Kodambakkam     0.040000               0  13.051520  80.224210
48                  Kilpauk     0.052632               0  13.081980  80.244480
43               Karapakkam     0.064516               0  12.915950  80.231920
108               Perungudi     0.057143               0  12.963550  80.239970
113                 Potheri     0.045455               0  12.823170  80.042830
114                  Pudhur     0.066667               0  13.043570  80.215080
115            Purasawalkam     0.044776               0  13.085250  80.253290
166           Virugambakkam     0.072727               0  13.055900  80.193490
165           Vinayagapuram     0.100000               0  13.127280  80.151110
162               Velachery     0.054945               0  12.979380  80.218430
160               Vanagaram     0.100000               0  13.063530  80.152230
158          Valasaravakkam     0.058824               0  13.041490  80.171560
157              Vadapalani     0.092308               0  13.052260  80.211200
156               Urapakkam     0.076923               0  12.863420  80.069160
39              Irumbuliyur     0.125000               0  12.914320  80.106040
155              Trustpuram     0.045455               0  13.058480  80.223950
146           Thiruvanmiyur     0.044444               0  12.986190  80.260510
145              Thiruporur     0.062500               0  12.942337  80.151345
139               Tharamani     0.100000               0  13.126868  80.230751
133        St. Thomas Mount     0.052632               0  13.007950  80.196080
128        Singaperumalkoil     0.111111               0  12.763330  80.003500
127          Sholinganallur     0.066667               0  12.897600  80.227950
124            Semmencherry     0.095238               0  12.865570  80.220510
148            Thuraipakkam     0.100000               0  12.903180  80.184550
38              Injambakkam     0.071429               0  12.926370  80.250250
84              Nanganallur     0.062500               0  12.976400  80.187600
169           West Mambalam     0.050000               0  13.038680  80.222850
23                  Choolai     0.047619               0  13.090240  80.265570
25                Chromepet     0.111111               0  12.952340  80.144110
17             Besant Nagar     0.056180               0  12.996850  80.266910
13              Ashok Nagar     0.072464               0  13.035390  80.212200
12               Arumbakkam     0.040000               0  13.073080  80.209520
10          Anna Nagar West     0.044444               0  13.092720  80.202220
9                Anna Nagar     0.040000               0  13.083590  80.210200
6                  Ambattur     0.083333               0  13.118820  80.154420
5           Alwarthirunagar     0.096774               0  13.050550  80.183970
37               ICF Colony     0.040541               0  13.0946

### Finally, let's visualize the resulting clusters

In [42]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(chennai_merged['Latitude'], chennai_merged['Longitude'], chennai_merged['Neighborhood'], chennai_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## 8. Examine Clusters

In [43]:
#Cluster 0
chennai_merged.loc[chennai_merged['Cluster Labels'] == 0]

Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
0           Adambakkam     0.083333               0  12.991920  80.206030
104           Perambur     0.083333               0  13.122470  80.235690
103     Peerkankaranai     0.111111               0  12.912240  80.098950
96              Pammal     0.086957               0  12.968140  80.133590
94          Pallavaram     0.111111               0  12.974440  80.148520
93      Palavanthangal     0.095238               0  12.986810  80.186730
91                Padi     0.045455               0  13.097560  80.186790
89            Nolambur     0.062500               0  13.076260  80.171690
88          Nesapakkam     0.090909               0  13.035210  80.191770
75        Meenambakkam     0.060606               0  12.986460  80.176000
74          Medavakkam     0.090909               0  12.920090  80.191630
64         Maduravoyal     0.125000               0  13.058410  80.166360
50         Kodungaiyur     0.100000               0  13.136630  80.244790
49         Kodambakkam     0.040000               0  13.051520  80.224210
48             Kilpauk     0.052632               0  13.081980  80.244480
43          Karapakkam     0.064516               0  12.915950  80.231920
108          Perungudi     0.057143               0  12.963550  80.239970
113            Potheri     0.045455               0  12.823170  80.042830
114             Pudhur     0.066667               0  13.043570  80.215080
115       Purasawalkam     0.044776               0  13.085250  80.253290
166      Virugambakkam     0.072727               0  13.055900  80.193490
165      Vinayagapuram     0.100000               0  13.127280  80.151110
162          Velachery     0.054945               0  12.979380  80.218430
160          Vanagaram     0.100000               0  13.063530  80.152230
158     Valasaravakkam     0.058824               0  13.041490  80.171560
157         Vadapalani     0.092308               0  13.052260  80.211200
156          Urapakkam     0.076923               0  12.863420  80.069160
39         Irumbuliyur     0.125000               0  12.914320  80.106040
155         Trustpuram     0.045455               0  13.058480  80.223950
146      Thiruvanmiyur     0.044444               0  12.986190  80.260510
145         Thiruporur     0.062500               0  12.942337  80.151345
139          Tharamani     0.100000               0  13.126868  80.230751
133   St. Thomas Mount     0.052632               0  13.007950  80.196080
128   Singaperumalkoil     0.111111               0  12.763330  80.003500
127     Sholinganallur     0.066667               0  12.897600  80.227950
124       Semmencherry     0.095238               0  12.865570  80.220510
148       Thuraipakkam     0.100000               0  12.903180  80.184550
38         Injambakkam     0.071429               0  12.926370  80.250250
84         Nanganallur     0.062500               0  12.976400  80.187600
169      West Mambalam     0.050000               0  13.038680  80.222850
23             Choolai     0.047619               0  13.090240  80.265570
25           Chromepet     0.111111               0  12.952340  80.144110
17        Besant Nagar     0.056180               0  12.996850  80.266910
13         Ashok Nagar     0.072464               0  13.035390  80.212200
12          Arumbakkam     0.040000               0  13.073080  80.209520
10     Anna Nagar West     0.044444               0  13.092720  80.202220
9           Anna Nagar     0.040000               0  13.083590  80.210200
6             Ambattur     0.083333               0  13.118820  80.154420
5      Alwarthirunagar     0.096774               0  13.050550  80.183970
37          ICF Colony     0.040541               0  13.094620  80.218390
34              Guindy     0.044118               0  13.004020  80.220210
35   Guindy TVK Estate     0.044118               0  13.004020  80.220210
1                Adyar     0.058824               0  13.003050  80.251930
2             

In [44]:
#Cluster 1
chennai_merged.loc[chennai_merged['Cluster Labels'] == 1]

Neighborhood  Pizza Place  Cluster Labels   Latitude  Longitude
159          Vallalar Nagar     0.000000               1  13.117310  80.059230
15                    Avadi     0.000000               1  13.129090  80.103610
126              Sholavaram     0.000000               1  13.235770  80.163690
125            Shenoy Nagar     0.030000               1  13.077320  80.224980
16               Ayanavaram     0.035714               1  13.098830  80.232380
123                Santhome     0.032787               1  13.029540  80.277620
122                Saidapet     0.032787               1  13.020260  80.221310
121           Sadayankuppam     0.000000               1  13.193190  80.291020
120               Royapuram     0.000000               1  13.113940  80.294200
119              Royapettah     0.020000               1  13.053500  80.268260
116                  Puzhal     0.000000               1  13.159460  80.207180
117          Puzhuthivakkam     0.000000               1  13.256470  80.304610
164             Villivakkam     0.000000               1  13.104910  80.206040
18          Chembarambakkam     0.000000               1  13.040270  80.064370
19             Chengalpattu     0.000000               1  12.682240  79.980080
112                   Porur     0.027027               1  13.030290  80.170160
111             Poonamallee     0.000000               1  13.051370  80.112660
110                 Ponneri     0.000000               1  13.165087  80.270677
109            Pondy Bazaar     0.000000               1  13.040850  80.238300
20                  Chepauk     0.014493               1  13.064400  80.280650
107           Perungalathur     0.000000               1  12.892790  80.065930
118               Red Hills     0.000000               1  13.195430  80.184310
14                Athipattu     0.000000               1  13.256700  80.291090
130           Sithalapakkam     0.000000               1  12.890140  80.184620
131               Sowcarpet     0.000000               1  13.091000  80.283430
4                  Alwarpet     0.000000               1  13.034710  80.254160
7               Aminjikarai     0.022222               1  13.071390  80.222560
8               Andarkuppam     0.000000               1  13.191590  80.273280
154              Triplicane     0.020000               1  13.062890  80.271460
153              Tondiarpet     0.000000               1  13.129230  80.289550
152                 Tolgate     0.000000               1  13.083620  80.282520
151            Tiruvottiyur     0.000000               1  13.141780  80.296920
150             Tiruverkadu     0.000000               1  13.056336  80.119199
161                Vandalur     0.000000               1  12.895300  80.088800
147          Thiruvidandhai     0.000000               1  12.759250  80.244110
129                Siruseri     0.000000               1  12.837580  80.201850
11                  Annanur     0.000000               1  13.112120  80.128950
143        Thirumullaivoyal     0.000000               1  13.127500  80.131640
142           Thirumazhisai     0.000000               1  13.052680  80.066720
141           Thirumangalam     0.034091               1  13.082850  80.196990
140              The Island     0.000000               1  13.101260  80.283790
163             Veppampattu     0.000000               1  13.120660  80.019190
138               Teynampet     0.000000               1  13.048200  80.249680
105            Periapalayam     0.000000               1  12.903156  80.159902
135                 Surapet     0.000000               1  13.148990  80.191540
134         Sunguvarchatram     0.000000               1  12.925990  79.879310
132           Sriperumbudur     0.000000               1  12.972335  80.042346
144           Thiruninravur     0.000000               1  13.119850  80.036010
136                T. Nagar     0.000000               1  13.045360  80.233900
36            Gummidipoondi     0.000000               1  13.4127

In [45]:
#Cluster 2
chennai_merged.loc[chennai_merged['Cluster Labels'] == 2]

Neighborhood  Pizza Place  Cluster Labels  Latitude  Longitude
167     Vyasarpadi     0.166667               2  13.11778   80.25168
106    Perumbakkam     0.250000               2  12.90563   80.20907
57   Kovilambakkam     0.200000               2  12.94047   80.18712
149      Tirusulam     0.153846               2  12.96906   80.17712
60     Madambakkam     0.200000               2  12.90529   80.15352
22    Chitlapakkam     0.200000               2  12.93277   80.14387
77       Mogappair     0.250000               2  13.08053   80.16116
78      Moolakadai     0.142857               2  13.12838   80.24086
47     Kelambakkam     0.200000               2  12.79341   80.22010
137       Tambaram     0.133333               2  12.92489   80.12818

# Observation

Most of Pizza shops are in Cluster 2 and very low count (close to zero) in Cluster 1 . Also, there are good opportunities to open near Park Town (City central place), Panagal park( Top shopping place in chennai) and Siruseri( IT Zone of chennai) in Cluster 1 . Looking at nearby venues, it seems Cluster 1 might be a good location as there are very less Pizza shops in these areas. Therefore, this project recommends the entrepreneur to open a Pizza shop in these locations with little to no competition. 